# Завдання 5. Рівняння Пуассона у декартових тривимірних координатах

Загальна форма рівняння:

$$
\frac{\partial^2 u}{\partial x^2} + \frac{\partial^2 u}{\partial y^2} + \frac{\partial^2 u}{\partial z^2} = f(x,y,z)
$$

Дискретизація:
$$
\frac{u_{i+1,j,k}^2-2u_{i,j,k}+u_{i-1,j,k}}{\Delta x^2} + \frac{u_{i,j+1,k}^2-2u_{i,j,k}+u_{i,j-1,k}}{\Delta y^2} + \frac{u_{i,j,k+1}^2-2u_{i,j,k}+u_{i,j,k-1}}{\Delta z^2} = f(x_i,y_j,z_k)
$$

$$
\frac{1}{\Delta x^{2}} u_{i+1,j,k} +\frac{1}{\Delta x^{2}} u_{i-1,j,k} +\frac{1}{\Delta y^{2}} u_{i,j+1,k} +\frac{1}{\Delta y^{2}} u_{i,j-1,k} +\frac{1}{\Delta z^{2}} u_{i,j+1,k} +\frac{1}{\Delta z^{2}} u_{i,j,k-1} -\left(\frac{2}{\Delta x^{2}} +\frac{2}{\Delta y^{2}} +\frac{2}{\Delta z^{2}}\right) u_{i,j,k} =f(x_{i} ,y_{j} ,z_{k} )
$$

Задача 5.8

$
\begin{cases}
x \in [1,2], \quad y \in [1,3], \quad z \in [0.5,1.5], \\
f(x,y,z) = e^{-x} - y + z, \\[4pt]
u(1,y,z) = 0, \quad \dfrac{\partial u}{\partial x}(2,y,z) = 1, \\[6pt]
u(x,1,z) + 2\dfrac{\partial u}{\partial y}(x,1,z) = 1, \quad u(x,3,z) = 0, \\[6pt]
u(x,y,0.5) = 0, \quad \dfrac{\partial u}{\partial z}(x,y,1.5) = 2.
\end{cases}
$

In [1]:
from solver import relax3d 
import numpy as np
import matplotlib.pyplot as plt

In [2]:
def f_fun(x, y, z):
    """Right-hand side f(x, y, z) = e^{-x} - y + z."""
    return np.exp(-x) - y + z

In [3]:
class Box3DGridConfig:
    def __init__(self,
                 nx=65, ny=65, nz=33,
                 xmin=1.0, xmax=2.0,
                 ymin=1.0, ymax=3.0,
                 zmin=0.5, zmax=1.5):

        self.nx, self.ny, self.nz = nx, ny, nz
        self.xmin, self.xmax = xmin, xmax
        self.ymin, self.ymax = ymin, ymax
        self.zmin, self.zmax = zmin, zmax

        # 1D grids
        self.x = np.linspace(xmin, xmax, nx)
        self.y = np.linspace(ymin, ymax, ny)
        self.z = np.linspace(zmin, zmax, nz)

        # spacings
        self.dx = self.x[1] - self.x[0]
        self.dy = self.y[1] - self.y[0]
        self.dz = self.z[1] - self.z[0]

        # 3D meshes
        self.XX, self.YY, self.ZZ = np.meshgrid(self.x, self.y, self.z, indexing='ij')

In [4]:
def assemble_system(cfg: Box3DGridConfig):
    nx, ny, nz = cfg.nx, cfg.ny, cfg.nz
    dx, dy, dz = cfg.dx, cfg.dy, cfg.dz

    inv_dx2 = 1.0 / (dx * dx)
    inv_dy2 = 1.0 / (dy * dy)
    inv_dz2 = 1.0 / (dz * dz)

    shape = (nx, ny, nz)

    # Coefficients for neighbors and main diagonal
    ax = np.full(shape, inv_dx2)  # coeff for u_{i-1,j,k}
    cx = np.full(shape, inv_dx2)  # coeff for u_{i+1,j,k}
    ay = np.full(shape, inv_dy2)  # coeff for u_{i,j-1,k}
    cy = np.full(shape, inv_dy2)  # coeff for u_{i,j+1,k}
    az = np.full(shape, inv_dz2)  # coeff for u_{i,j,k-1}
    cz = np.full(shape, inv_dz2)  # coeff for u_{i,j,k+1}
    b  = np.full(shape, 2.0 * (inv_dx2 + inv_dy2 + inv_dz2))  # diagonal

    # Right-hand side
    d_rhs = f_fun(cfg.XX, cfg.YY, cfg.ZZ)

    # -------------------------------
    # 1) Dirichlet boundaries
    # -------------------------------
    # u(1,y,z)     = 0      at x = xmin (i = 0)
    # u(x,3,z)     = 0      at y = ymax (j = ny-1)
    # u(x,y,0.5)   = 0      at z = zmin (k = 0)


    # -------------------------------
    # 2) Neumann at x = 2: ∂u/∂x = 1
    # -------------------------------
    iR = nx - 2
    cx_old = cx[iR, :, :].copy()
    cx[iR, :, :] = 0.0
    b[iR, :, :] -= cx_old * 1.0
    d_rhs[iR, :, :] -= cx_old * dx  # g=1 ⇒ C = g*dx = dx

    # -------------------------------
    # 3) Robin at y = 1: u + 2 u_y = 1
    # -------------------------------
    jB = 1
    A_robin = -2.0 / (dy - 2.0)
    C_robin =  dy / (dy - 2.0)

    ay_old = ay[:, jB, :].copy()
    ay[:, jB, :] = 0.0
    b[:, jB, :] -= ay_old * A_robin
    d_rhs[:, jB, :] -= ay_old * C_robin

    # -------------------------------
    # 4) Neumann at z = 1.5: ∂u/∂z = 2
    # -------------------------------
    kT = nz - 2
    cz_old = cz[:, :, kT].copy()
    cz[:, :, kT] = 0.0
    b[:, :, kT] -= cz_old * 1.0
    d_rhs[:, :, kT] -= cz_old * (2.0 * dz)  # g=2 ⇒ C = 2*dz
    return ax, ay, az, cx, cy, cz, b, d_rhs

In [5]:
def apply_boundary_values(U, cfg: Box3DGridConfig):
    nx, ny, nz = cfg.nx, cfg.ny, cfg.nz
    dx, dy, dz = cfg.dx, cfg.dy, cfg.dz

    # x = 1 (Dirichlet)
    U[0, :, :] = 0.0

    # x = 2 (Neumann du/dx = 1)
    U[nx - 1, :, :] = U[nx - 2, :, :] + dx

    # y = 3 (Dirichlet)
    U[:, ny - 1, :] = 0.0

    # y = 1 (Robin u + 2 u_y = 1)
    U[:, 0, :] = (dy - 2.0 * U[:, 1, :]) / (dy - 2.0)

    # z = 0.5 (Dirichlet)
    U[:, :, 0] = 0.0

    # z = 1.5 (Neumann du/dz = 2)
    U[:, :, nz - 1] = U[:, :, nz - 2] + 2.0 * dz

    return U

In [6]:
nx, ny, nz = 65, 65, 33


cfg = Box3DGridConfig(nx=nx, ny=ny, nz=nz)

ax, ay, az, cx, cy, cz, b, d_rhs = assemble_system(cfg)

U0 = np.zeros((cfg.nx, cfg.ny, cfg.nz))
U0 = apply_boundary_values(U0, cfg)

U = relax3d(
    ax, ay, az, cx, cy, cz, b, d_rhs,
    cfg.nx, cfg.ny, cfg.nz, U0,
    omega=1.84, eps=1e-13, max_iter=50000,
    min_iter=100,
)

U_final = apply_boundary_values(U, cfg)

iter= 500 err= 0.00016450892326203004
iter= 1000 err= 1.1531313823809342e-06
iter= 1500 err= 8.050518474078672e-09
iter= 2000 err= 5.62045965324387e-11
iter= 2500 err= 3.9412917374193057e-13
Converged in 2641 iterations. Final error: 9.903189379656396e-14


In [7]:
import plotly.graph_objects as go
x_vec, y_vec, z_vec = cfg.x, cfg.y, cfg.z

XX, YY, ZZ = np.meshgrid(x_vec, y_vec, z_vec, indexing='ij')

fig = go.Figure(data=go.Isosurface(
    x=XX.flatten(), y=YY.flatten(), z=ZZ.flatten(),
    value=U_final.flatten(),
    isomin=U_final.min(), isomax=U_final.max(),
    surface_count=6,         
    colorscale='Viridis',
    opacity=0.7,             
    caps=dict(x_show=False, y_show=False, z_show=False)
))
fig.update_layout(scene=dict(xaxis_title='x', yaxis_title='y', zaxis_title='z'),
                  title='Isosurfaces of U(x,y,z)')
fig.show()


In [8]:
# --- Verification ----------------------------------------------------------
pde_residual = np.zeros_like(U_final)
dx, dy, dz = cfg.dx, cfg.dy, cfg.dz
# 1) PDE residual on interior: ax*U_{i-1}+cx*U_{i+1}+... - b*U_{i,j,k} - d_rhs = 0
for i in range(1, nx-1):
    for j in range(1, ny-1):
        for k in range(1, nz-1):
            lap_disc = ( ax[i,j,k]*U_final[i-1,j,k] + cx[i,j,k]*U_final[i+1,j,k]
                       + ay[i,j,k]*U_final[i, j-1, k] + cy[i,j,k]*U_final[i, j+1, k]
                       + az[i,j,k]*U_final[i, j, k-1] + cz[i,j,k]*U_final[i, j, k+1]
                       - b[i,j,k]*U_final[i,j,k] )
            pde_residual[i,j,k] = lap_disc - d_rhs[i,j,k]

# 2) Boundary conditions
# x=1: Dirichlet u=0
bc_x_min = np.abs(U_final[0, 1:-1, 1:-1])

# x=2: Neumann du/dx = 1
bc_x_max = np.abs((U_final[nx-1,1:-1,1:-1] - U_final[nx-2,1:-1,1:-1]) / dx - 1.0)

# y=3: Dirichlet u=0
bc_y_max = np.abs(U_final[1:-1, ny-1, 1:-1])

# y=1: Robin u + 2 du/dy = 1
bc_y_min = np.abs(U_final[1:-1,0,1:-1] + 2.0*(U_final[1:-1,1,1:-1] - U_final[1:-1,0,1:-1]) / dy - 1.0)

# z=0.5: Dirichlet u=0
bc_z_min = np.abs(U_final[1:-1, 1:-1, 0])

# z=1.5: Neumann du/dz = 2
bc_z_max = np.abs((U_final[1:-1, 1:-1, nz-1] - U_final[1:-1, 1:-1, nz-2]) / dz - 2.0)

# 3) Summary
print("--- Verification Results (3D box) ---")
print(f"PDE residual (interior) : {np.max(np.abs(pde_residual[1:-1,1:-1,1:-1])): .3e}")
print(f"BC x=1 (Dirichlet)      : {np.max(bc_x_min): .3e}")
print(f"BC x=2 (Neumann)        : {np.max(bc_x_max): .3e}")
print(f"BC y=3 (Dirichlet)      : {np.max(bc_y_max): .3e}")
print(f"BC y=1 (Robin)          : {np.max(bc_y_min): .3e}")
print(f"BC z=0.5 (Dirichlet)    : {np.max(bc_z_min): .3e}")
print(f"BC z=1.5 (Neumann)      : {np.max(bc_z_max): .3e}")

--- Verification Results (3D box) ---
PDE residual (interior) :  2.093e-10
BC x=1 (Dirichlet)      :  0.000e+00
BC x=2 (Neumann)        :  1.421e-14
BC y=3 (Dirichlet)      :  0.000e+00
BC y=1 (Robin)          :  1.110e-14
BC z=0.5 (Dirichlet)    :  0.000e+00
BC z=1.5 (Neumann)      :  7.105e-15
